# Basic Query Parallelism

## <span style="color:#0b486b">Preliminary</span>

### Scenario Background

Imagine you're working for a large hospital network that is part of a global healthcare group. This network maintains comprehensive records on patients, doctors, diagnoses, treatments, and costs associated with each visit. The hospital has branches across multiple regions, and it deals with a high volume of patient data generated daily. The data collected includes details about patient visits, the diagnoses made by doctors, the treatments prescribed, and the cost associated with these treatments.

As the hospital network expands, it faces challenges related to efficiently managing and analyzing the increasing volume of healthcare data. This is where big data technologies and parallel query processing come into play. The task at hand is to implement parallelism techniques to improve the speed and efficiency of querying large datasets across multiple regions. Your assignment is to develop and optimize parallel queries to extract meaningful insights from the dataset.

### Dataset

In this assignment, you are provided 6 `.csv` files to help you answer the questions in each section. The following details the information about the dataset.

#### main.csv
* uuid [record_id] (an integer-based unique identifier to each record/row)
* patient_id (an integer-based identifier of patient, foreign key to patient.csv)
* doctor_id (an integer-based identifier of doctor, foreign key to doctor.csv)
* diagnosis (string with a word that describes the diagnosis)
* treatment (string that describes the treatments)
* visit_date (date and time corresponding to patient visit)
* treatment_cost (cost of the treatment, stored as float)

#### delta.csv
* contains same columns as in **main.csv** but with one additional column.
* The addtional column is called operations (with 3 possible string value, *update*, *insert* and *delete*)

#### patient.csv
* uuid [patient_id] (an integer-based unique identifier to each patient)
* name (string that contains the name of the patient)
* age (an integer value that describes the age of the patient)
* gender (only 2 possible string values present, *male* and *female*)
* address (string that contains the address of the patient)

#### doctor.csv
* uuid [doctor_id] (an integer-based unique identifier to each doctor)
* name (string that contains the name of the doctor)
* specialty (string that describes the specialty of the doctor)
* hospital_id (an integer-based identifier to each hospital branch, foreign key to hospital.csv)

#### hospital.csv
* uuid [hospital_id] (an integer-based unique identifier to each hospital branch)
* name (string that contains the name of the hospital)
* location (string that states at where the hospital situated)

#### impl.csv
* uuid (a string-based unique identifier)
* random_string (column contains random string value)
* random_int (column contains random integer value)

### Required Imports

Import necessary Python modules in the cell below.

In [1]:
import csv
from collections import defaultdict
from multiprocessing import Pool
from pathlib import Path
from typing import (
    Any,
    Dict,
    ItemsView,
    KeysView,
    List,
    Optional,
    Tuple,
    Union,
    ValuesView,
    Callable,
)
from functools import partial

from dateutil.parser import ParserError, parse

######### START YOUR CODE HERE #########
from pprint import pprint
import heapq
from datetime import datetime
########## END YOUR CODE HERE ##########

### Basic Query Parallelism

Load the necessary dataset into memory.

In [2]:
def map_type(values: List[str]) -> List[Any]:
    try:
        return list(map(int, values))
    except ValueError:
        pass

    try:
        return list(map(float, values))
    except ValueError:
        pass

    try:
        return list(map(parse, values))
    except ParserError:
        return values


def read_csv(file: Path) -> Dict[str, List[Any]]:
    results = defaultdict(list)

    with file.open(mode="r", encoding="utf8", newline="") as file:
        reader = csv.DictReader(file)
        for row in reader:
            for key, value in row.items():
                results[key].append(value)

    results = {k: map_type(v) for k, v in results.items()}
    return results


class Dataset:
    def __init__(
        self,
        *,
        file_path: Optional[Path] = None,
        data: Optional[Dict[str, List[Any]]] = None,
    ):
        assert (file_path is None) != (data is None)

        self.data = read_csv(file_path) if file_path else data
        self._count = 0

    def __getitem__(
        self,
        key: Union[str, int, Tuple[str, Union[int, slice]], slice],
    ) -> Union[List[Any], Any]:
        if isinstance(key, str):
            return self.data[key]
        elif isinstance(key, int):
            return {k: self[k, key] for k in self.keys()}
        elif isinstance(key, slice):
            start = key.start if key.start else 0
            stop = key.stop if key.stop else len(self)
            step = key.step if key.step else 1

            start += len(self) if start < 0 else 0
            stop += len(self) if stop < 0 else 0
            return [self[idx] for idx in range(start, stop, step)]
        elif isinstance(key, tuple):
            assert len(key) == 2

            key_idx, elem_idx = key
            return self.data[key_idx][elem_idx]
        else:
            raise ValueError

    def __iter__(self):
        self._count = 0
        return self

    def __next__(self):
        if (index := self._count) >= len(self):
            raise StopIteration
        self._count += 1
        return self[index]

    def __len__(self) -> int:
        return len(next(iter(self.values()))) if len(self.data) else 0

    def __repr__(self) -> str:
        return repr(self.data)

    def keys(self) -> KeysView[str]:
        return self.data.keys()

    def values(self) -> ValuesView[List[Any]]:
        return self.data.values()

    def items(self) -> ItemsView[str, List[Any]]:
        return self.data.items()

In [3]:
# Modify the path following your folder structure
root_dir = Path("/home/student/Assignment 1/data")

# Load the data
main_data = Dataset(file_path=(root_dir / "main.csv"))

######### START YOUR CODE HERE #########
# file_path = root_dir / "main.csv"
# print("File exists:", file_path.exists())
# print("Full path:", file_path.resolve())

impl_data = Dataset(file_path=(root_dir / "impl.csv"))
delta_data = Dataset(file_path=(root_dir / "delta.csv"))
doctor_data = Dataset(file_path=(root_dir / "doctor.csv"))
patient_data = Dataset(file_path=(root_dir / "patient.csv"))
hospital_data = Dataset(file_path=(root_dir / "hospital.csv"))

########## END YOUR CODE HERE ##########

## <span style="color:#0b486b">Part 1: Parallel Search Algorithms</span>
This section consists of **4 sub-questions**.

In this task, you will study the effect of parallelism on search query. You also demonstrate your programming skills by developing linear search and parallel search algorithms that will be used to search and filter the data with better efficiency.

### Task 1.1 Linear Search

Implement a multi-attribute linear search algorithm. There are two types of searching algorithm, namely column-based searching and row-based searching. 

#### Column-based Searching
The following is the pseudocode of column-based searching.

> def column_search(table, attr_1='a', attr_2=100):</br>
  >> find all occurrences of attr_1 in table and extract the data</br>
  >> find all occurrences of attr_2 in table and extract the data</br>
  >> return intersection of them</br>

#### Row-based Searching
The following is the pseudocode for row-based searching

> def row_search(table, attr_1='b', attr_2=10):</br>
  >> Iterate through each of the row</br>
  >> Check if the row has attr_1 and attr_2</br>
  >> return all row that satisfy the conditions</br>

***Based on the above descriptions, select one of the scheme to implement your search algorithms.***

**Hint**: The function signature of the linear search is provided in the cell below. Note that basic_crit has the following structure
```json
[
  {"attr_1": "some_value", "attr_2": "some_value"},
  {"attr_1": "some_value"},
  {"attr_3": "somve_value"}
]
```
The structure corresponds to basic query (checking if the value of the attribute matches the provided value in the query). Note that every condition within a dictionary is evaluated using **AND** operator and the result from each dictionary is evaluated using **OR** operator. In addition, to implement sophisticated query, advanced_crit should be provided which is a function that returns boolean value.

In [4]:
def linear_search(
    data: Dataset,
    *,
    basic_crit: Optional[List[Dict[str, Any]]] = None,
    advanced_crit: Optional[Callable[..., bool]] = None,
) -> Dataset:
    assert basic_crit is not None or advanced_crit is not None
    result = defaultdict(list)

    ######### START YOUR CODE HERE #########
    for idx in range(len(data)):
        row = {k: data[k][idx] for k in data.keys()}

        match_basic = False
        if basic_crit:
            for condition in basic_crit:
                if all(row.get(k) == v for k, v in condition.items()):
                    match_basic = True
                    break  

        match_advanced = advanced_crit(row) if advanced_crit else False

        if match_basic or match_advanced:
            for k in data.keys():
                val = data[k][idx]
                if hasattr(val, "strftime"):
                    val = val.strftime("%Y-%m-%d %H:%M:%S")
                result[k].append(val)

    result = Dataset(data=dict(result))
    ########## END YOUR CODE HERE ##########

    return result

### Task 1.2 Parallel Search

Implement a multi-attribute parallel search algorithm. In this task, you have to extend the linear search into a parallel search algorithm using hash-based partition.

**Hint**: The function `hash_partition` will be used in subsequent parts.

In [5]:
def hash_func(*args: List[Any], **kwargs: Dict[str, Any]) -> int:
    result = None
    
    ######### START YOUR CODE HERE #########
    combined = tuple(args) + tuple(sorted(kwargs.items()))
    result = hash(combined)
    ########## END YOUR CODE HERE ##########
    
    return result

def hash_partition(
    data: Dataset,
    n: int,
    *args: List[Any],
    **kwargs: Dict[str, Any],
) -> List[Dataset]:
    partitions = [defaultdict(list) for _ in range(n)]
    
    ######### START YOUR CODE HERE #########
    for row_idx, row in enumerate(data):
        hash_args = [row[arg] if isinstance(arg, str) and arg in row else arg for arg in args]
        hash_kwargs = {key: row[value] if isinstance(value, str) and value in row else value for key, value in kwargs.items()}
        
        partition_idx = abs(hash_func(*hash_args, **hash_kwargs)) % n
        
        for col_name, col_value in row.items():
            partitions[partition_idx][col_name].append(col_value)
    
    partitions = [Dataset(data=dict(partition)) for partition in partitions]
    ########## END YOUR CODE HERE ##########
    
    return partitions

In [6]:
def partition_search(partition, basic_crit=None, advanced_crit=None):
    return linear_search(
        data=partition,
        basic_crit=basic_crit,
        advanced_crit=advanced_crit
    )

def parallel_search(
    data: Dataset,
    n_processor: int,
    *,
    basic_crit: Optional[List[Dict[str, Any]]] = None,
    advanced_crit: Optional[Callable[..., Any]] = None,
) -> Dataset:
    pool = Pool(processes=n_processor)
    result = None
    
    ######### START YOUR CODE HERE #########
    partitions = hash_partition(data, n_processor)
    
    async_results = [
        pool.apply_async(partition_search, (partition,), 
                        {'basic_crit': basic_crit, 'advanced_crit': advanced_crit})
        for partition in partitions
    ]
    
    search_results = [res.get() for res in async_results]
    
    combined_data = defaultdict(list)
    for part_result in search_results:
        if part_result:
            for key, values in part_result.items():
                combined_data[key].extend(values)
    
    result = Dataset(data=dict(combined_data))
    ########## END YOUR CODE HERE ##########
    return result

### Task 1.3 Practical Question

In this section, use the searching algorithm to run queries as shown below.
* Task 1.3.1 `impl.csv`
    * Task 1.3.1.1 - Find records where *random_string='u22o5o' or random_int=200* 
    * Task 1.3.1.2 - Find records where each digit in *random_int* exists in *random_string*
        * ('a4oe4', 4) should be returned since 'a4oe4' contains 4
        * ('4i52o', 52) should be returned since '4i52o' contains 5 and 2
        * ('5ae11', 21) should not be returned since '5ae11' does not contain 2

* Task 1.3.2 `main.csv`
    * Task 1.3.2.1 - Find all patient records where *diagnosis='covid-19'* and *treatment_cost <= 100*
    * Task 1.3.2.2 - Retrieve records of surgery from 2023-02-01 to 2024-02-28
    * Task 1.3.2.3 - Find all records where *doctor_id=patient_id* and *diagnosis='asthma'*

Each query should be completed in separate cells

String comparison should be case-insensitive.

**Hint**: For advanced query, define a function with the following signature
```python
def func(*args: List[Any], **kwargs: Dict[str, Any]) -> bool:
    pass
```

#### Task 1.3.1 impl.csv

##### Task 1.3.1.1 
Find records where *random_string='u22o5o' or random_int=200*

In [7]:
######### START YOUR CODE HERE #########
criteria = [{"random_string": "u22o5o"}, {"random_int": 200}]
results = parallel_search(impl_data,3, basic_crit=criteria)
results
########## END YOUR CODE HERE ##########

{'uuid': ['459285d7-b8e0-4722-9b54-3b8bc331233b'], 'random_string': ['u22o5o'], 'random_int': [71]}

##### Task 1.3.1.2
Find records where each digit in *random_int* exists in *random_string*

In [8]:
######### START YOUR CODE HERE #########
def digit_in_string_criteria(row: Dict[str, Any]) -> bool:
    int_digits = list(str(row["random_int"]))
    string = row["random_string"]
    return all(d in string for d in int_digits)

results = parallel_search(impl_data,3, advanced_crit=digit_in_string_criteria)
results
########## END YOUR CODE HERE ##########

{'uuid': ['b3b4c5d0-8711-483a-bd17-01b2c5162dc5', '71b17b45-5344-4cb7-9172-7686e1a4e05e', 'ec2fd1ef-e0ac-4ff8-bdf3-172788a2b579', 'eacf41b1-d5ef-4371-95a8-aaa1da1df751', 'd19de232-1ea3-4f38-8cfa-6d3a0aa385d3', '95755b9c-dbd1-4186-8822-3ae63ad1d47e', '88c79aec-efac-4f0e-8079-4f62d4f66ef7', '131a35f1-ec25-4a80-ab9d-268b887a292e', 'aba77527-ffb8-4ce6-827e-96b0dd40e4b2', 'c5eed61d-6412-4d91-ad29-793989f28e26', 'fc3bbcde-e008-48ef-9b44-ca1df52b1454', '5df125c9-cfcb-4a78-82c4-d33e2a69682d', '987785a3-5f0d-4a72-9e55-f62af4a49301', 'faa6bc71-5a7e-44e0-a0b6-282455005769', '4c9e9696-0748-4c29-bcb8-9a1d4a318e01', '01364612-f6ad-47da-b4f0-a13089208b1a', '47c9466c-59a4-4204-94af-298ebc31fb2d', '285ecb85-4c03-4a4d-99ad-1b03d6e8aaf9', 'b93eebfa-f7c4-4889-a81a-2ea918bf8d18', 'd799c63a-dd1e-4cf4-94bc-660611b6cbae', '14ae25e6-0fb8-431a-8b03-02aee3cbc09b', '818e08aa-6746-44b1-8bf5-c224025a997b', 'b523e7d8-bbfc-4244-b0d2-d346c80b3503', 'aac6147e-b72d-460c-8904-cb7b92721dda', '0b4633bb-136c-4e2b-9bf2-17db8

#### Task 1.3.2 main.csv

##### Task 1.3.2.1
Find all patient records where *diagnosis='covid-19'* and *treatment_cost <= 100*

In [9]:
######### START YOUR CODE HERE #########
def covid_and_cost(row: Dict[str, Any]) -> bool:
    return row["diagnosis"].lower() == "covid-19" and row["treatment_cost"] <= 100

results = parallel_search(main_data,2, advanced_crit=covid_and_cost)
results
########## END YOUR CODE HERE ##########

{'uuid': [12, 67, 174, 199, 223, 226, 227, 296, 341, 480, 521, 596, 656, 691, 723, 747, 778, 795, 824, 901, 940, 987, 1022, 1137, 1142, 1145, 1148, 1157, 1162, 1207, 1223, 1233, 1265, 1357, 1377, 1446, 1467, 1485, 1523, 1525, 1568, 1649, 1686, 1836, 1848, 1921, 1943, 1954, 1959, 1963, 1983, 2044, 2101, 2129, 2204, 2265, 2327, 2343, 2348, 2421, 2540, 2547, 2561, 2588, 2649, 2842, 2908, 2931, 3046, 3051, 3052, 3133, 3153, 3156, 3178, 3203, 3221, 3235, 3268, 3376, 3380, 3497, 3533, 3547, 3555, 3575, 3602, 3611, 3618, 3709, 3726, 3738, 3776, 3781, 3863, 3938, 3951, 4015, 4029, 4049, 4053, 4096, 4146, 4177, 4286, 4348, 4357, 4390, 4492, 4557, 4559, 4571, 4576, 4615, 4622, 4665, 4732, 4739, 4753, 4800, 4811, 5131, 5168, 5224, 5302, 5314, 5367, 5439, 5479, 5530, 5551, 5560, 5583, 5698, 5703, 5761, 5861, 5870, 5925, 5934, 6004, 6010, 6048, 6064, 6109, 6168, 6182, 6347, 6348, 6456, 6472, 6502, 6587, 6665, 6703, 6719, 6735, 6810, 6926, 6961, 7023, 7031, 7062, 7068, 7076, 7155, 7171, 7199, 7229, 

##### Task 1.3.2.2
Retrieve records of surgery from 2023-02-01 to 2024-02-28

In [10]:
######### START YOUR CODE HERE #########
def surgery_in_date_range(row: Dict[str, Any]) -> bool:
    if "surgery" in row["treatment"].lower():
        visit_date = row["visit_date"]
        if isinstance(visit_date, str):
            visit_date = parse(visit_date)
        return datetime(2023, 2, 1) <= visit_date <= datetime(2024, 2, 28)
    return False

results = parallel_search(main_data,2, advanced_crit=surgery_in_date_range)
results
########## END YOUR CODE HERE ##########

{'uuid': [73, 92, 360, 408, 410, 560, 574, 611, 628, 761, 789, 808, 862, 911, 913, 937, 1031, 1061, 1128, 1149, 1296, 1303, 1404, 1449, 1478, 1567, 1585, 1723, 1735, 1738, 1843, 1893, 1936, 1942, 1973, 1975, 1998, 2053, 2054, 2091, 2174, 2205, 2209, 2357, 2569, 2676, 2741, 2758, 2820, 2838, 2839, 2850, 2860, 2887, 2896, 2902, 3030, 3077, 3209, 3214, 3281, 3294, 3316, 3332, 3440, 3490, 3508, 3544, 3583, 3591, 3601, 3614, 3697, 3717, 3820, 3832, 3867, 4089, 4207, 4218, 4354, 4375, 4599, 4627, 4660, 4702, 4827, 4938, 4951, 5038, 5066, 5104, 5139, 5153, 5194, 5210, 5225, 5252, 5300, 5397, 5404, 5470, 5472, 5528, 5595, 5600, 5671, 5700, 5715, 5846, 5968, 5984, 6139, 6194, 6204, 6223, 6315, 6325, 6495, 6512, 6523, 6547, 6570, 6597, 6601, 6610, 6612, 6695, 6710, 6780, 6796, 6917, 6922, 6952, 6988, 7028, 7077, 7165, 7312, 7323, 7490, 7558, 7564, 7592, 7677, 7727, 7774, 7833, 7888, 7921, 7935, 7945, 7977, 7991, 8075, 8077, 8113, 8131, 8133, 8143, 8264, 8281, 8282, 8309, 8339, 8443, 8470, 8493, 

##### Task 1.3.2.3
Find all records where *doctor_id=patient_id* and *diagnosis='asthma'*

In [11]:
######### START YOUR CODE HERE #########
def doc_equals_patient_with_asthma(row: Dict[str, Any]) -> bool:
    return row["doctor_id"] == row["patient_id"] and row["diagnosis"].lower() == "asthma"

results = parallel_search(main_data,3, advanced_crit=doc_equals_patient_with_asthma)
results
########## END YOUR CODE HERE ##########

{'uuid': [26272], 'patient_id': [4], 'doctor_id': [4], 'diagnosis': ['Asthma'], 'treatment': ['Observation'], 'visit_date': ['2024-02-23 14:40:08'], 'treatment_cost': [78.92]}

### Task 1.4 Theoretical Question

Answer the following questions with table having *m* rows and *n* columns
* Based on the selected searching scheme, explain what happens when
    * $m \gg n$
    * $n \gg m$
    * What optimization can be done to address the issues?
* If the query is single-attribute, what optimization can be done in hash-based parallel searching algorithm implemented above?

#### Solution

<span>When implementing search algorithms over tabular data, the structure of the dataset—specifically the number of rows (𝑚) and columns (𝑛)—plays a significant role in the performance and efficiency of the search. Depending on whether the dataset is row-dominant (𝑚 ≫ 𝑛) or column-dominant (𝑛 ≫ 𝑚), different implications and optimization strategies arise.

In the first case, when 𝑚 ≫ 𝑛, the table has a large number of rows but relatively few columns. This is a typical scenario in real-world datasets where millions of records are collected but each record contains only a limited number of fields. In such a structure, performing row-based linear search may result in performance bottlenecks, as each row needs to be iterated and evaluated against the search conditions. The algorithm becomes CPU-intensive due to the volume of data it must process. To optimize performance in this case, parallelism becomes highly beneficial. Techniques such as hash-based partitioning allow the data to be split across multiple processors, enabling concurrent evaluation of search conditions. Additionally, data indexing and early filtering strategies can significantly reduce the number of rows that need to be examined.

On the other hand, when 𝑛 ≫ 𝑚, the dataset contains many columns but only a few rows. In this situation, the row-based search remains efficient, as the number of records is limited and can be traversed quickly. However, if a column-based search strategy were used instead, performance might degrade. Extracting and comparing values across a high number of columns increases memory usage and processing time. To address this, column pruning—which involves evaluating only the necessary columns relevant to the query—can be applied to reduce computation overhead. In this context, maintaining a row-based search is the optimal choice for its simplicity and speed.

Furthermore, in scenarios where the query is based on a single attribute, additional optimizations can be applied to the hash-based parallel search algorithm. Specifically, partitioning the dataset based on the hash value of the queried attribute ensures that all matching records are directed to the same processor. This localized processing reduces unnecessary inter-process comparisons and speeds up result retrieval. For example, if the query searches for records with doctor_id = 5, using doctor_id as the hashing key directs all relevant rows into a single partition, which can then be searched efficiently.

In conclusion, the efficiency of a search algorithm is greatly influenced by the structure of the dataset and the nature of the query. When rows vastly outnumber columns, leveraging parallel processing and partitioning is essential. Conversely, when columns exceed rows, preserving a row-based approach and avoiding unnecessary column scans can prevent performance degradation. Finally, tailoring partitioning strategies to single-attribute queries can significantly enhance parallel search performance. Understanding these structural nuances allows for more intelligent algorithm design, ultimately improving the responsiveness and scalability of data processing systems.</span>

## <span style="color:#0b486b">Part 2: Parallel Join Algorithms</span>
This section consists of **2 sub-questions**.

In this task, you will study the effect of parallelism on join query. You also demonstrate your programming skills by developing parallel join algorithm that will be used to join the data with better efficiency.

### Task 2.1 Parallel Join

Implement Duplication Outer Join Algorithm (DOJA). The algorithm consists of 4 main steps.
* (Replication): Duplicate small table
* (Local Inner Join): Perform inner join in each processor
* (Distribution): Reshuffle inner join result based on R.x
* (Local Outer Join): Perform outer join between initial table R and inner join result

In your implementation, clearly differentiate the columns from left table and columns from right table. The resulting table should have all columns from both table with labels like **left** and **right** for clarity.

**Hint**: The function *hash_join* is to return the hash value for matching the records in the join operation. For data distribution, please use *hash_partition* from previous section. Also note that the argument *join* should be one of the strings ['inner', 'left', 'right', 'full']

In [12]:
def hash_join(*args: List[Any], **kwargs: Dict[str, Any]) -> int:
    result = 0
    ######### START YOUR CODE HERE #########
    for arg in args:
        result ^= hash(arg)
    for key, value in kwargs.items():
        result ^= hash((key, value))
    ########## END YOUR CODE HERE ##########
    
    return result

def serial_join(
    data_l: Dataset,
    data_r: Dataset,
    *,
    join: str = "inner",
    left_attributes: List[str] = ["uuid"],
    right_attributes: List[str] = ["uuid"],
) -> Dataset:
    assert join in ["left", "right", "full", "inner"]
    assert len(left_attributes) == len(right_attributes)
    result = defaultdict(list)
    ######### START YOUR CODE HERE #########
    left_rows = list(data_l)
    right_rows = list(data_r)
    
    right_index = {}
    for r in right_rows:
        key = tuple(r[attr] for attr in right_attributes)
        right_index.setdefault(key, []).append(r)
    
    has_left_rows = bool(left_rows)
    has_right_rows = bool(right_rows)
    
    for l_row in left_rows:
        l_key = tuple(l_row[attr] for attr in left_attributes)
        matches = right_index.get(l_key, [])
        
        if matches or join in ["left", "full"]:
            if not matches and join in ["left", "full"]:
                combined = {f"{k}_left": v for k, v in l_row.items()}
                if has_right_rows:
                    combined.update({f"{k}_right": None for k in right_rows[0].keys()})
                for col, val in combined.items():
                    result[col].append(val)
            else:
                for r_row in matches:
                    combined = {f"{k}_left": v for k, v in l_row.items()}
                    combined.update({f"{k}_right": v for k, v in r_row.items()})
                    for col, val in combined.items():
                        result[col].append(val)
    
    if join in ["right", "full"]:
        left_keys = {tuple(l[attr] for attr in left_attributes) for l in left_rows}
        
        for r_row in right_rows:
            r_key = tuple(r_row[attr] for attr in right_attributes)
            if r_key not in left_keys:
                combined = {f"{k}_right": v for k, v in r_row.items()}
                if has_left_rows:
                    combined.update({f"{k}_left": None for k in left_rows[0].keys()})
                for col, val in combined.items():
                    result[col].append(val)
    ######### END YOUR CODE HERE #########
    return result

In [13]:
def local_inner_join(
    large_partition: Dataset,
    small_table: Dataset,
    left_attrs: List[str],
    right_attrs: List[str],
) -> Dataset:
    """Perform a local inner join between a partition and the small table."""
    result = defaultdict(list)
    
    small_index = defaultdict(list)
    for i in range(len(small_table)):
        key = tuple(small_table[attr][i] for attr in right_attrs)
        small_index[key].append(i)

    for i in range(len(large_partition)):
        l_key = tuple(large_partition[attr][i] for attr in left_attrs)
        if l_key in small_index:
            for j in small_index[l_key]:
                for col in large_partition.keys():
                    result[f"{col}_left"].append(large_partition[col][i])
                for col in small_table.keys():
                    result[f"{col}_right"].append(small_table[col][j])
    
    return Dataset(data=dict(result))

In [14]:
def doja(
    data_l: Dataset,
    data_r: Dataset,
    n_process: int,
    *,
    join: str = "left",
    left_attributes: List[str] = ["uuid"],
    right_attributes: List[str] = ["uuid"],
) -> Dataset:
    assert join in ["left", "right", "full"]
    result = []
    
    ######### START YOUR CODE HERE #########
    # Step 1: Identify smaller table for broadcast
    if len(data_l) <= len(data_r):
        small_table, large_table = data_l, data_r
        small_attrs, large_attrs = left_attributes, right_attributes
        small_is_left = True
    else:
        small_table, large_table = data_r, data_l
        small_attrs, large_attrs = right_attributes, left_attributes
        small_is_left = False
    
    # Step 2: Partition the large table
    partitions = hash_partition(large_table, n_process, *large_attrs)
    
    # Step 3: Parallel inner joins
    with Pool(n_process) as pool:
        async_results = [
            pool.apply_async(local_inner_join, args=(p, small_table, large_attrs, small_attrs))
            for p in partitions
        ]
        inner_results = [res.get() for res in async_results]

    # Step 4: Merge inner join results
    merged_inner = defaultdict(list)
    for res in inner_results:
        for col, vals in res.items():
            merged_inner[col].extend(vals)
    merged_inner = Dataset(data=dict(merged_inner))
    
    # Step 5: Handle outer join logic
    if join == "inner":
        return merged_inner
    
    matched_left_keys = set(zip(*[merged_inner[f"{attr}_left"] for attr in left_attributes]))
    matched_right_keys = set(zip(*[merged_inner[f"{attr}_right"] for attr in right_attributes]))
    
    final_rows = []
    for i in range(len(merged_inner)):
        row = {}
        for col in merged_inner.keys():
            row[col] = merged_inner[col][i]
        final_rows.append(row)
    
    if join in ["left", "full"]:
        left_rows = list(data_l)
        for l_row in left_rows:
            l_key = tuple(l_row[attr] for attr in left_attributes)
            if l_key not in matched_left_keys:
                row = {f"{k}_left": v for k, v in l_row.items()}
                for col in data_r.keys():
                    row[f"{col}_right"] = None
                final_rows.append(row)
    
    if join in ["right", "full"]:
        right_rows = list(data_r)
        for r_row in right_rows:
            r_key = tuple(r_row[attr] for attr in right_attributes)
            if r_key not in matched_right_keys:
                row = {f"{k}_right": v for k, v in r_row.items()}
                for col in data_l.keys():
                    row[f"{col}_left"] = None
                final_rows.append(row)
    
    if join == "full":
        for row in final_rows:
            for attr in left_attributes:
                left_val = row.get(f"{attr}_left")
                right_val = row.get(f"{attr}_right")
                row[attr] = left_val if left_val is not None else right_val
                row.pop(f"{attr}_left", None)
                row.pop(f"{attr}_right", None)
    
    final_data = defaultdict(list)
    if final_rows:
        for col in final_rows[0].keys():
            for row in final_rows:
                final_data[col].append(row.get(col))
        result = Dataset(data=dict(final_data))
    ########## END YOUR CODE HERE ##########
    
    result = Dataset(data=dict(result))
    return result

### Task 2.2 Practical Question

In this question, use DOJA algorithm to answer the following questions.
* Task 2.2.1 - Join *main.csv* and *delta.csv*
    * Use *uuid* as the join attribute
    * Based on the value in column named operation in *delta.csv*
        * Insert the row to *main.csv* if operation is *insert*
        * Update the row using information from *delta.csv* if operation is *update*
        * Delete the row from *main.csv* if operation is *delete*
* Task 2.2.2 - Left Outer Join updated *main.csv* with
    * *doctor.csv*
    * *patient.csv*
* Task 2.2.3 - Right Outer Join *doctor.csv* with *hospital.csv*

The output of the Outer Join should follow the following structure
```python
{
    "column_1_left": [...],
    "column_2_left": [...],
    "column_1_right": [...],
    "column_2_right": [...]
}
```

**Hint**: The function *delta_update* is used to answer the first question. The other two questions can be answered using DOJA directly. Each question should be completed in each cell.

##### Task 2.2.1

Join main.csv and delta.csv

In [15]:
def delta_update(main_table: Dataset, delta_table: Dataset) -> Dataset:
    ######### START YOUR CODE HERE #########
    # Process delete operations
    delete_uuids = []
    for i in range(len(delta_table)):
        if delta_table['operation'][i] == 'delete':
            delete_uuids.append(delta_table['uuid'][i])
    
    # Filter out deleted rows from main table
    if delete_uuids:
        main_data = {col: [] for col in main_table.keys()}
        for i in range(len(main_table)):
            if main_table['uuid'][i] not in delete_uuids:
                for col in main_table.keys():
                    main_data[col].append(main_table[col][i])
        main_table = Dataset(data=main_data)
    
    # Extract update operations
    update_rows = []
    for i in range(len(delta_table)):
        if delta_table['operation'][i] == 'update':
            row = {}
            for col in delta_table.keys():
                row[col] = delta_table[col][i]
            update_rows.append(row)
    
    # Create update dataset
    if update_rows:
        update_data = {}
        for col in set().union(*(row.keys() for row in update_rows)):
            update_data[col] = [row.get(col) for row in update_rows]
        update_ops = Dataset(data=update_data)
        
        # Join main table with update operations using doja
        updated_main = doja(
            main_table, 
            update_ops, 
            4,
            join="left",
            left_attributes=["uuid"],
            right_attributes=["uuid"]
        )
        
        # Merge the updated values
        merged_data = {col: [] for col in main_table.keys()}
        for i in range(len(updated_main)):
            for col in main_table.keys():
                right_col = f"{col}_right"
                left_col = f"{col}_left"
                
                if right_col in updated_main.keys():
                    right_val = updated_main[right_col][i]
                    left_val = updated_main[left_col][i]
                    merged_data[col].append(right_val if right_val is not None else left_val)
                else:
                    merged_data[col].append(updated_main[left_col][i])
        
        main_table = Dataset(data=merged_data)
    
    # Process insert operations
    insert_rows = []
    for i in range(len(delta_table)):
        if delta_table['operation'][i] == 'insert':
            row = {}
            for col in delta_table.keys():
                if col != 'operation':
                    row[col] = delta_table[col][i]
            insert_rows.append(row)
    
    if insert_rows:
        insert_data = {col: main_table[col].copy() for col in main_table.keys()}
        
        for row in insert_rows:
            for col in main_table.keys():
                insert_data[col].append(row.get(col))
        
        main_table = Dataset(data=insert_data)
    
    return main_table
    ########## END YOUR CODE HERE ##########
    
#51098
updated_data = delta_update(main_data, delta_data)
updated_data

{'uuid': [11, 31, 155, 180, 211, 225, 256, 267, 290, 304, 385, 408, 478, 506, 540, 630, 636, 686, 709, 762, 771, 779, 785, 799, 883, 897, 934, 951, 1004, 1010, 1018, 1035, 1041, 1142, 1198, 1232, 1235, 1243, 1260, 1288, 1319, 1392, 1527, 1541, 1676, 1679, 1713, 1727, 1755, 1772, 1828, 1842, 1856, 1952, 1955, 2070, 2115, 2132, 2174, 2191, 2250, 2261, 2292, 2295, 2357, 2391, 2531, 2607, 2641, 2672, 2697, 2756, 2773, 2776, 2790, 2832, 2863, 2897, 2931, 2973, 3015, 3018, 3026, 3029, 3080, 3147, 3167, 3195, 3251, 3296, 3313, 3344, 3364, 3378, 3403, 3423, 3426, 3440, 3448, 3555, 3583, 3651, 3656, 3732, 3791, 3800, 3808, 3811, 3842, 3856, 3887, 3943, 3963, 4019, 4061, 4095, 4171, 4202, 4205, 4236, 4323, 4351, 4396, 4430, 4483, 4520, 4537, 4573, 4579, 4587, 4607, 4621, 4638, 4649, 4722, 4742, 4801, 4804, 4812, 4852, 4863, 4894, 5001, 5088, 5091, 5136, 5141, 5178, 5181, 5195, 5203, 5217, 5220, 5293, 5338, 5361, 5372, 5479, 5510, 5552, 5563, 5586, 5611, 5628, 5645, 5659, 5670, 5701, 5732, 5780, 

##### Task 2.2.2

Left outer join updated main.csv with doctor.csv

In [30]:
######### START YOUR CODE HERE #########
left_join_doctor = doja(updated_data, doctor_data, 
                        4, join='left', 
                        left_attributes=['doctor_id'], 
                        right_attributes=['uuid'])

# len(left_join_doctor)
# 51098
left_join_doctor

import pandas as pd

data = pd.DataFrame(left_join_doctor)
data.sort_values(by=list(data.columns))
########## END YOUR CODE HERE ##########

uuid_left  patient_id_left  doctor_id_left diagnosis_left  \
15905          1             3372              75       Fracture   
31261          2             2344             148       Diabetes   
43663          3              353              88        Allergy   
30856          4             2956             187       Fracture   
31644          5             1019              35       Fracture   
...          ...              ...             ...            ...   
42625      59954               23              66       Migraine   
51097      59961             2499              81       Diabetes   
42626      59974             4792             103            Flu   
42627      59980              698              18        Allergy   
42628      59994             3408              97     Depression   

         treatment_left     visit_date_left  treatment_cost_left  uuid_right  \
15905  Physical Therapy 2020-05-28 20:12:39               130.52          75   
31261        Medication 2020-06-28 04:25:49               139.85         148   
43663        Medication 2023-04-28 13:25:18               307.38          88   
30856  Physical Therapy 2021-12-27 19:42:06               358.03         187   
31644           Surgery 2022-07-08 11:45:14               957.11          35   
...                 ...                 ...                  ...         ...   
42625        Medication 2020-11-13 05:35:04               166.91          66   
51097        Medication 2024-03-18 08:59:42               413.13          81   
42626        Medication 2020-04-02 23:02:22               296.25         103   
42627       Observation 2024-05-30 11:49:14                57.97          18   
42628        Medication 2022-02-18 13:50:54                88.14          97   

       name_right     specialty_right  hospital_id_right  
15905   Doctor_75         Orthopedics                  4  
31261  Doctor_148  Allergy/Immunology                  1  
43663   Doctor_88  Allergy/Immunology                  3  
30856  Doctor_187          Psychiatry                  5  
31644   Doctor_35         Orthopedics                  2  
...           ...                 ...                ...  
42625   Doctor_66           Neurology                  1  
51097   Doctor_81       Endocrinology                  1  
42626  Doctor_103          Pediatrics                  4  
42627   Doctor_18  Allergy/Immunology                  4  
42628   Doctor_97          Psychiatry                  1  

[51098 rows x 11 columns]

Left outer join updated main.csv with patient.csv

In [31]:
######### START YOUR CODE HERE #########
joined_outer_patient = doja(
    updated_data,
    patient_data,
    n_process=4,
    join="left",
    left_attributes=["patient_id"],
    right_attributes=["uuid"]
)
# len(joined_outer_patient)
# 51098
joined_outer_patient

data = pd.DataFrame(joined_outer_patient)
data.sort_values(by=list(data.columns))
########## END YOUR CODE HERE ##########

uuid_left  patient_id_left  doctor_id_left diagnosis_left  \
1634           1             3372              75       Fracture   
26736          2             2344             148       Diabetes   
27144          3              353              88        Allergy   
776            4             2956             187       Fracture   
14517          5             1019              35       Fracture   
...          ...              ...             ...            ...   
25596      59954               23              66       Migraine   
38379      59961             2499              81       Diabetes   
51096      59974             4792             103            Flu   
51097      59980              698              18        Allergy   
25597      59994             3408              97     Depression   

         treatment_left     visit_date_left  treatment_cost_left  uuid_right  \
1634   Physical Therapy 2020-05-28 20:12:39               130.52        3372   
26736        Medication 2020-06-28 04:25:49               139.85        2344   
27144        Medication 2023-04-28 13:25:18               307.38         353   
776    Physical Therapy 2021-12-27 19:42:06               358.03        2956   
14517           Surgery 2022-07-08 11:45:14               957.11        1019   
...                 ...                 ...                  ...         ...   
25596        Medication 2020-11-13 05:35:04               166.91          23   
38379        Medication 2024-03-18 08:59:42               413.13        2499   
51096        Medication 2020-04-02 23:02:22               296.25        4792   
51097       Observation 2024-05-30 11:49:14                57.97         698   
25597        Medication 2022-02-18 13:50:54                88.14        3408   

         name_right  age_right gender_right address_right  
1634   Patient_3372         39       Female   813 Main St  
26736  Patient_2344         22       Female   908 Main St  
27144   Patient_353         22       Female   952 Main St  
776    Patient_2956          4       Female   991 Main St  
14517  Patient_1019         25       Female   133 Main St  
...             ...        ...          ...           ...  
25596    Patient_23         91       Female   718 Main St  
38379  Patient_2499         81         Male   456 Main St  
51096  Patient_4792         27         Male   341 Main St  
51097   Patient_698         25         Male   812 Main St  
25597  Patient_3408         96         Male   838 Main St  

[51098 rows x 12 columns]

##### Task 2.2.3
Right outer join doctor.csv with hospital.csv

In [32]:
######### START YOUR CODE HERE #########
joined_doctor_hospital = doja(
    doctor_data,
    hospital_data,
    n_process=2,
    join="right",
    left_attributes=["hospital_id"],
    right_attributes=["uuid"]
)

#len(joined_doctor_hospital)
#200
joined_doctor_hospital

data = pd.DataFrame(joined_doctor_hospital)
data.sort_values(by=list(data.columns))
########## END YOUR CODE HERE ##########

uuid_left   name_left      specialty_left  hospital_id_left  uuid_right  \
86           1    Doctor_1       Endocrinology                 2           2   
0            2    Doctor_2          Cardiology                 3           3   
1            3    Doctor_3          Pediatrics                 3           3   
2            4    Doctor_4         Pulmonology                 3           3   
87           5    Doctor_5         Orthopedics                 5           5   
..         ...         ...                 ...               ...         ...   
197        196  Doctor_196           Neurology                 2           2   
84         197  Doctor_197          Psychiatry                 3           3   
198        198  Doctor_198  Allergy/Immunology                 1           1   
199        199  Doctor_199     General Surgery                 1           1   
85         200  Doctor_200         Dermatology                 4           4   

     name_right location_right  
86   Hospital_2        Houston  
0    Hospital_3      San Diego  
1    Hospital_3      San Diego  
2    Hospital_3      San Diego  
87   Hospital_5    San Antonio  
..          ...            ...  
197  Hospital_2        Houston  
84   Hospital_3      San Diego  
198  Hospital_1    San Antonio  
199  Hospital_1    San Antonio  
85   Hospital_4        Phoenix  

[200 rows x 7 columns]

## <span style="color:#0b486b">Part 3: Parallel Sort Algorithms</span>
This section consists of **3 sub-questions**

In this task, you will study the effect of parallelism on sorting query. You also demonstrate your programming skills by developing parallel sorting algorithm that will be used to join data with better efficiency.

#### Task 3.1 Parallel Binary Merge-Sort

In this task, you will implement parallel binary merge-sort. Parallel Binary Merge-Sort contains 2 phases, namely
* Task 3.1.1 - Local Sort
* Task 3.1.2 - Final Merge

The first phase is similar to parallel merge-all sort that is taught in the applied session. The second phase, on the other hand, is pipelined instead of concentrating on one processor. In this phase, we take the results from 2 processors and then merge them in one processor, called binary merging. The result of the merge between two processors is passed on to the next level until one processor is left.

**Hint**: In this task, round_robin partition is used. The argument *key* in the sorting function is simply a function that returns the value to be compared during sorting and merging. The value corresponds to the columns that is used for sorting.

In [19]:
def round_robin_partition(data: Dataset, n_process: int) -> Dataset:
    result = [defaultdict(list) for _ in range(n_process)]

    ######### START YOUR CODE HERE #########
    num_rows = len(data)
    
    for i in range(num_rows):
        partition_idx = i % n_process
        row = data[i]  
        for key, value in row.items():
            result[partition_idx][key].append(value)
    
    result = [Dataset(data=dict(partition)) for partition in result]
    ########## END YOUR CODE HERE ##########

    return result


def k_way_merge(
    data_set: List[Union[List[Dict[str, Any]], Dataset]],
    key: Callable[[Dict[str, Any]], Any],
) -> Dataset:
    indices = [0 for _ in range(len(data_set))]
    result = defaultdict(list)

    ######### START YOUR CODE HERE #########
    datasets = []
    for ds in data_set:
        if isinstance(ds, Dataset):
            datasets.append(list(ds))  
        else:
            datasets.append(ds)
    
    result = defaultdict(list)
    
    heap = []
    
    for i, ds in enumerate(datasets):
        if len(ds) > 0:
            heapq.heappush(heap, (key(ds[0]), i, 0, ds[0]))
    
    while heap:
        _, ds_idx, row_idx, row = heapq.heappop(heap)
        
        for col, val in row.items():
            result[col].append(val)
    
        if row_idx + 1 < len(datasets[ds_idx]):
            next_row = datasets[ds_idx][row_idx + 1]
            heapq.heappush(heap, (key(next_row), ds_idx, row_idx + 1, next_row))
    
    result = Dataset(data=dict(result))
    ########## END YOUR CODE HERE ##########

    return result

In [20]:
def serial_sorting(
    dataset: Dataset,
    *,
    buffer_size: int,
    key: Callable[[Dict[str, Any]], Any],
) -> Dataset:
    if buffer_size <= 2:
        raise AttributeError
    ######### START YOUR CODE HERE #########
    rows = list(dataset)
    
    sorted_runs = []
    for i in range(0, len(rows), buffer_size):
        chunk = rows[i:i + buffer_size]
        sorted_chunk = sorted(chunk, key=key)
        
        chunk_data = defaultdict(list)
        for row in sorted_chunk:
            for k, v in row.items():
                chunk_data[k].append(v)
        sorted_runs.append(Dataset(data=dict(chunk_data)))
    
    if len(sorted_runs) > 1:
        while len(sorted_runs) > 1:
            new_runs = []
            for i in range(0, len(sorted_runs), buffer_size):
                batch = sorted_runs[i:i + buffer_size]
                if len(batch) > 1:
                    merged = k_way_merge(batch, key)
                    new_runs.append(merged)
                elif len(batch) == 1:
                    new_runs.append(batch[0])
            
            sorted_runs = new_runs
        
        result = sorted_runs[0]
    else:
        result = sorted_runs[0] if sorted_runs else Dataset(data={})
    ########## END YOUR CODE HERE ##########
    return result

In [21]:
def sort_partition_helper(args):
    partition, buffer_size, key = args
    return serial_sorting(partition, buffer_size=buffer_size, key=key)

def parallel_binary_merge_sort(
    dataset: Dataset,
    n_processor: int,
    *,
    buffer_size: int,
    key: Callable[[Dict[str, Any]], Any],
) -> Dataset:
    if buffer_size <= 2:
        raise AttributeError
    ######### START YOUR CODE HERE #########
    # Step 1: Round-robin partitioning
    partitions = round_robin_partition(dataset, n_processor)
    
    # Step 2: Sort each partition in parallel
    inner_tasks = [(partitions[i], buffer_size, key) for i in range(n_processor)]
    
    with Pool(processes=n_processor) as pool:
        # Use apply_async for each task
        jobs = [pool.apply_async(sort_partition_helper, args=(task,)) for task in inner_tasks]
        
        # Wait for all tasks to complete and collect results
        sorted_partitions = [job.get() for job in jobs]
    
    # Step 3: Merge all sorted partitions in a single k-way merge
    if sorted_partitions:
        result = k_way_merge(sorted_partitions, key)
    else:
        result = Dataset(data={})
    
    ########## END YOUR CODE HERE ##########
    return result

### Task 3.2 Practical Question

Using the parallel sorting algorithm to answer the following questions.
* Task 3.2.1 - Find the top-10 treatment cost, reported together with the diagnosis and treatment
* Task 3.2.2 - Report the total visits for each (doctor, patient) pair

Only the columns specified in the question is included in the final output. For example, the total visits for each (doctor, patient) pair has the following structure
```python
{
    "doctor_id": [...],
    "patient_id": [...],
    "visit_count": [...]
}
```

**Hint**: Each question should be answered in each cell. You may need to apply additional operation on the dataset to obtain the final results.

##### Task 3.2.1

Find the top-10 treatment cost, reported together with the diagnosis and treatment

In [22]:
def key(row):
        return row["treatment_cost"]
    
def get_top_n_treatment_costs(dataset, n=10, num_partitions=4, buffer_size=3):
    # Sort the data by treatment cost in ascending order
    sorted_data = parallel_binary_merge_sort(
        dataset, 
        n_processor=num_partitions, 
        buffer_size=buffer_size, 
        key=key
    )
    
    # Get the top-n most expensive treatments (last n elements after sort)
    top_n_rows = sorted_data[-n:]
    
    # Prepare columnar data structure
    result_columns = defaultdict(list)
    
    for row in top_n_rows:
        result_columns["diagnosis"].append(row["diagnosis"])
        result_columns["treatment"].append(row["treatment"])
        result_columns["treatment_cost"].append(row["treatment_cost"])
    
    return Dataset(data=dict(result_columns))

# Usage example:
top_10_treatments = get_top_n_treatment_costs(main_data)
top_10_treatments

{'diagnosis': ['Diabetes', 'Hypertension', 'Fracture', 'Arthritis', 'Diabetes', 'Allergy', 'Hypertension', 'Asthma', 'Arthritis', 'Hypertension'], 'treatment': ['Medication', 'Medication', 'Physical Therapy', 'Medication', 'Medication', 'Observation', 'Medication', 'Medication', 'Medication', 'Medication'], 'treatment_cost': [1755.56, 1759.31, 1769.51, 1845.64, 1865.27, 1887.95, 1917.59, 1929.22, 1929.97, 1980.7]}

##### Task 3.2.2
Report the total visits for each (doctor, patient) pair

In [23]:
######### START YOUR CODE HERE #########
def visit_key(row):
    return (row["doctor_id"], row["patient_id"])

def count_doctor_patient_visits(dataset, num_processors=3, buffer_size=3):

    sorted_data = parallel_binary_merge_sort(
        dataset,
        n_processor=num_processors,
        buffer_size=buffer_size,
        key=visit_key
    )

    visit_counts = defaultdict(int)

    for row in sorted_data:
        doctor_patient_pair = visit_key(row)  
        visit_counts[doctor_patient_pair] += 1

    visit_stats = {
        "doctor_id": [],
        "patient_id": [],
        "visit_count": [],
    }

    for (doctor_id, patient_id), count in visit_counts.items():
        visit_stats["doctor_id"].append(doctor_id)
        visit_stats["patient_id"].append(patient_id)
        visit_stats["visit_count"].append(count)

    return Dataset(data=visit_stats)
# Usage example:
visit_counts = count_doctor_patient_visits(main_data)
len(visit_counts)
########## END YOUR CODE HERE ##########

48286

### Task 3.3 Theoretical Question

Based on the implementation of parallel binary-merge, answer the following.
* Does the algorithm utilize all available processors? State and justify with respect to each phase: sorting and merging phases
* Approximate the computational complexity of the algorithm in big-O notation

#### Solution

# Parallel Binary Merge-Sort Analysis

### 1. Does the algorithm utilize all available processors?

**Sorting Phase:**
- **Round-robin partitioning**: The dataset is divided into `n_processor` partitions using the `round_robin_partition` function. This ensures that the dataset is evenly distributed across all available processors. For a dataset of size `N` and `n_processor` processors, each processor will handle roughly `N/n_processor` rows.
- **Parallel Sorting**: The sorting of each partition is done in parallel using Python's `multiprocessing.Pool`. The `serial_sorting` function is applied to each partition in parallel, making use of all available processors. Specifically, the `Pool` is used to distribute sorting tasks across `n_processor` processes. Therefore, the algorithm **does utilize all available processors** during the sorting phase, with each processor independently sorting a partition of the dataset.

**Merging Phase:**
- **Pipelined Binary Merging**: In this phase, the algorithm merges pairs of partitions in a binary tree-like pattern. Each iteration merges two partitions, and the result is passed along to the next round of merging. This process continues until only one partition remains.
- The binary merging happens sequentially after the initial parallel sorting phase, meaning that while all processors are used in the sorting phase, the merging is a series of sequential steps with fewer parallel opportunities. This could be considered a limitation in terms of fully utilizing all processors in the merging phase, as the number of partitions is halved with each merge.

**Conclusion:**
- **Sorting Phase**: The algorithm fully utilizes all available processors as it distributes sorting tasks across them.
- **Merging Phase**: The merging phase is a pipelined process that reduces the number of active partitions with each round of merging. While each round of merging involves some parallelism (merging adjacent partitions), this phase doesn't leverage all available processors as efficiently as the sorting phase because the number of active partitions decreases after each merge.

Thus, **the algorithm uses all processors in the sorting phase**, but **the merging phase does not make full use of all processors** due to the sequential nature of binary merging.

---

### 2. Computational Complexity (Big-O Notation)

**Sorting Phase:**
- **Time Complexity of `round_robin_partition`:** The partitioning step involves iterating over all `N` rows and distributing them into `n_processor` partitions. This takes **O(N)** time, where `N` is the number of rows in the dataset.
- **Time Complexity of `serial_sorting`:** For each partition, the `serial_sorting` function performs an external merge sort. Sorting each partition of size `N/n_processor` takes **O((N/n_processor) log (N/n_processor))** time. Since there are `n_processor` partitions, the total time complexity for the sorting phase is:
  \[
  O\left(n\_processor \times \frac{N}{n\_processor} \log \frac{N}{n\_processor}\right) = O(N \log (N/n\_processor))
  \]
  This simplifies to **O(N log N)** because `n_processor` is a constant factor, and the logarithmic term dominates. Thus, the sorting phase has **O(N log N)** complexity.

**Merging Phase:**
- **Time Complexity of `k_way_merge`:** The merging step uses a min-heap to merge two partitions at a time. Merging two partitions of size `M` takes **O(M log M)** time. Since there are `N` elements in total and the merging follows a binary tree structure, the total number of merge steps is **log(n_processor)** (since partitions halve with each merge). Therefore, the time complexity of the merging phase is **O(N log n_processor)**, where `N` is the number of rows.

**Total Computational Complexity:**
- The total time complexity of the algorithm is dominated by the sorting phase and the merging phase. Combining the complexities of both phases:
  - Sorting phase: **O(N log N)**
  - Merging phase: **O(N log n_processor)**

Since **log n_processor** is smaller than **log N**, the overall time complexity is dominated by the sorting phase. Thus, the total computational complexity is:

\[
O(N \log N)
\]

This complexity is typical of sorting algorithms, and although parallelism improves performance, the overall time complexity still follows the **O(N log N)** form due to the nature of sorting.

---

### Conclusion:
- **Does the algorithm utilize all processors?**: The algorithm utilizes all available processors in the sorting phase, but the merging phase does not fully leverage all processors because of its sequential binary merge pattern.
- **Computational Complexity**: The overall complexity of the algorithm is **O(N log N)**, dominated by the sorting phase. The merging phase adds a smaller complexity of **O(N log n_processor)**.



## <span style="color:#0b486b">Part 4: Parallel Groupby Algorithms</span>
This section consists of **2 sub-questions**.

In this task, you will study the effect of parallelism on groupby query. You also demonstrate your programming skills by developing parallel groupby algorithm that will be used to group the data with better efficiency.

### Task 4.1 Parallel GroupBy with Merge-All

In this task, you will implement parallel groupby with merge-all method. It involves the following two steps:
* Task 4.1.1 - Local aggregate in each processor
* Task 4.1.2 - Global aggregation

In [24]:
def get_default(value: Any) -> Any:
    return value

def serial_groupby(
    dataset: Dataset,
    *,
    group_keys: List[str],
    value_key: str,
    operation: Callable[[Any, Any], Any],
    default_value: Any = 0,
) -> Dict[str, Any]:
    result = defaultdict(partial(get_default, default_value))
    
    ######### START YOUR CODE HERE #########
    for i in range(len(dataset)):
        group = tuple(dataset[key][i] for key in group_keys)
        value = dataset[value_key][i]
        result[group] = operation(result[group], value)
    ########## END YOUR CODE HERE ##########
    return result

In [25]:
def groupby_partition_helper(args) -> Dict[str, Any]:
    partition, group_keys, value_key, operation, default_value = args
    return serial_groupby(
        partition,
        group_keys=group_keys,
        value_key=value_key,
        operation=operation,
        default_value=default_value
    )

def parallel_merge_all_groupby(
    dataset: Dataset,
    n_process: int,
    *,
    group_keys: List[str],
    value_key: str,
    operation: Callable[[Any, Any], Any],
    default_value: Any = 0,
) -> Dict[str, Any]:
    ######### START YOUR CODE HERE #########
    partitions = hash_partition(dataset, n_process, *group_keys)
    
    tasks = [(partition, group_keys, value_key, operation, default_value) for partition in partitions]
    
    with Pool(processes=n_process) as pool:
        jobs = [pool.apply_async(groupby_partition_helper, (task,)) for task in tasks]
        partial_results = [job.get() for job in jobs]
    
    merged = defaultdict(lambda: default_value)
    for partial_result in partial_results:
        for group_key, value in partial_result.items():
            merged[group_key] = operation(merged[group_key], value)
    
    result = {key: [] for key in group_keys}
    result[value_key] = []
    
    for group_key, agg_value in merged.items():
        for i, key in enumerate(group_keys):
            result[key].append(group_key[i])
        result[value_key].append(agg_value)
    ########## END YOUR CODE HERE ##########
    return result

### Task 4.2 Practical Questions

Use the parallel join and groupby algorithm to answer the following questions.
* Task 4.2.1 - Compute the total treatment cost earned by each hospital
* Task 4.2.2 - Compute the average treatment cost of (doctor, diagnosis) pair
* Task 4.2.3 - Compute the total treatment cost paid by each patient in each hospital

Ensure the output follows the following structure
```python
{
    "group_key_1": [...],
    "group_key_2": [...],
    "value_key": [...]
}
```
where `group_key` is the columns that are used for grouping operation and `value_key` is the column that is used for aggregation.

##### Task 4.2.1
Compute the total treatment cost earned by each hospital

In [26]:
######### START YOUR CODE HERE #########
def sum_cost(x, y):
    return round(x + y, 2)

def groupby_sum_treatment_cost_by_hospital(main_data: Dataset, doctor_data: Dataset, n_process: int = 4) -> Dict[str, Any]:
    # Perform left join on doctor_id
    joined_data = doja(main_data, doctor_data, n_process, join="left", left_attributes=["doctor_id"])

    # Prepare groupby-compatible dataset
    final_output = Dataset(data={
        'hospital_id': [entry['hospital_id_right'] for entry in joined_data],
        'treatment_cost': [entry['treatment_cost_left'] for entry in joined_data]
    })

    # Run parallel groupby aggregation
    result = parallel_merge_all_groupby(
        final_output,
        n_process,
        group_keys=['hospital_id'],
        value_key='treatment_cost',
        operation=sum_cost,
        default_value=0
    )

    return result

result = groupby_sum_treatment_cost_by_hospital(main_data, doctor_data)
result
########## END YOUR CODE HERE ##########

{'hospital_id': [3, 5, 4, 1, 2],
 'treatment_cost': [2184796.71,
  2158588.72,
  3466114.43,
  2605109.58,
  2047072.54]}

##### Task 4.2.2
Compute average treatment cost of (doctor, diagnosis) pair

In [33]:
######### START YOUR CODE HERE #########
def avg_cost(x, y):
   if isinstance(x, tuple) and isinstance(y, tuple):
       return (x[0] + y[0], x[1] + y[1])
   elif isinstance(x, tuple):
       return (x[0] + y, x[1] + 1)
   else:
       return (y, 1)

def groupby_avg_treatment_cost_by_doctor_diagnosis(main_data: Dataset, n_process: int = 4) -> Dataset:
   # Directly extract only needed columns
   final_output = Dataset(data={
       'doctor_id': main_data['doctor_id'],
       'diagnosis': main_data['diagnosis'],
       'treatment_cost': main_data['treatment_cost']
   })
   
   # Run parallel groupby using tuple accumulation for average
   grouped = parallel_merge_all_groupby(
       final_output,
       n_process,
       group_keys=['doctor_id', 'diagnosis'],
       value_key='treatment_cost',
       operation=avg_cost,
       default_value=(0, 0)
   )
   
   # Calculate averages from accumulated sums and counts
   result = {k: v for k, v in grouped.items()}
   result['treatment_cost'] = [
       round(total / count, 2) if count > 0 else 0
       for total, count in grouped['treatment_cost']
   ]
   
   return Dataset(data=result)

result = groupby_avg_treatment_cost_by_doctor_diagnosis(main_data)
#200
result

data = pd.DataFrame(result)
data.sort_values(by=list(data.columns))
########## END YOUR CODE HERE ##########

doctor_id     diagnosis  treatment_cost
109          1      Diabetes          255.76
9            2  Hypertension          260.14
1            3           Flu          255.57
81           4        Asthma          253.16
88           4      Covid-19          243.88
..         ...           ...             ...
91         195     Arthritis          250.70
23         195      Fracture          230.97
180        196      Migraine          250.95
153        197    Depression          262.88
138        198       Allergy          269.38

[200 rows x 3 columns]

##### Task 4.2.3
Compute the total treatment cost paid by each patient in each hospital

In [34]:
def calculate_treatment_cost_by_patient_and_hospital(
    main_data: Dataset,
    doctor_data: Dataset,
    n_process: int = 4
) -> Dataset:

    joined_data = doja(
        main_data, 
        doctor_data, 
        n_process, 
        join="left", 
        left_attributes=["doctor_id"],
        right_attributes=["uuid"]
    )
    
    final_output = Dataset(data={
        'patient_id': [entry['patient_id_left'] for entry in joined_data],
        'hospital_id': [entry['hospital_id_right'] for entry in joined_data],
        'treatment_cost': [entry['treatment_cost_left'] for entry in joined_data]
    })
    

    aggregated_results = parallel_merge_all_groupby(
        final_output,
        n_process,
        group_keys=['patient_id', 'hospital_id'],
        value_key='treatment_cost',
        operation=sum_cost,
        default_value=0
    )
    
    # Create and return final dataset
    result = Dataset(data=aggregated_results)
    ########## END YOUR CODE HERE ##########
    
    return result

result = calculate_treatment_cost_by_patient_and_hospital(main_data, doctor_data)
#21318
data = pd.DataFrame(result)
data.sort_values(by=list(data.columns))

patient_id  hospital_id  treatment_cost
11932           1            1          438.42
9081            1            2          565.04
444             1            3         1411.72
12569           1            4          709.94
21076           1            5          494.11
...           ...          ...             ...
9777         4999            5          788.63
15496        5000            2          238.26
932          5000            3          934.28
16263        5000            4         1139.52
6595         5000            5         1226.96

[21318 rows x 3 columns]